# Numerical Solution of Nonlinear Equations

TMA4125 Vår 2022

This notebook accompanies the slides [04-Nonlinear-Equations.pdf](https://www.math.ntnu.no/emner/TMA4125/2022v/lecture-notes/04-Nonlinear-Equations.pdf).

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
from numpy.linalg import solve, norm
import math

In [ ]:
# The function from Example 1
def f(x):
    return x**3+x**2-3*x-3

In [ ]:
# Try plotting yourself

In [ ]:
# We could also just check numerically
[f(-math.sqrt(3)), f(-1), f(math.sqrt(3))]

## Bisection method
The algorithms for the bisection method (Sliode #6) looks like

In [ ]:
def bisection(f, a, b, tol=1.0e-6, max_iter = 100, verbose=True):
    """
        bisection(f, a, b, tol=1e-6, maxiter=100)
    
    Solve the scalar equation f(x) = 0 by bisection.
    
    Input:
        f    - the function
        a, b - the interval
    Optional (keyword arguments)
        tol  - (`1.0e-6`) a tolerance when to stop due to a small intervall
        max_iter – (`100`) a maximal number of iterations
        verbose – (`True`) activates printing if set to true
    Output:
        r, k – the found root and the number of iterations needed
               to get to this point
    """
    fa = f(a)
    fb = f(b)
    if fa*fb > 0:
        print('Error: f(a)*f(b)>0, there may be no root in the interval.')
        return 0, 0
    for k in range(max_iter):
        c = 0.5*(a+b)               # The midpoint
        fc = f(c)                   
        verbose and print('k={:3d}, a={:.6f}, b={:.6f}, c={:10.6f}, f(c)={:10.3e}'
              .format(k, a, b, c, fc)) 
        if abs(f(c)) < 1.e-14:
            verbose and print("The value f(c) is very close to zero")
            break 
        elif (b-a) < 2*tol: # The zero is found!
            verbose and print("The point c_k is close to r (less than {:.6f}).".format((b-a)/2))
            break 
        elif fa*fc < 0:               
            b = c                   # There is a root in [a, c]
        else:
            a = c                   # There is a root in [c, b]  
    return c, k

In [ ]:
# The function from Example 1
def f(x):
    return x**3+x**2-3*x-3
# On a smaller intervall
a, b = 1.5, 2
c, nit = bisection(f, a, b, tol=1.e-4) # Apply the bisecetion method

## Fixpoint iteration

The algorithm from slide #8 reads

In [ ]:
def fixpoint(g, x0, tol=1.e-8, max_iter=30, verbose=True):
    """
        x, k = fixpoint(g, x0, tol=1.e-8, max_iter=30)
    
    Solve the fix point equation $x=g(x)$ by ix point iterations.
    The result of each iteration can be printed (and is by default)
    
    Input:
        g        – the function g(x)
        x0       - the initial value
    Optional (keyword) arguments
        tol      - (`1.0e-8`) a tolerance when to stop
        max_iter - (`30`) the maximal number of iterations
        verbose  – (`True`) prints the iterates if set to true
    Output:
        x, k – the found root and the number of iterations needed
               to get to this point
    """
    #   tol: The tolerance
    # Output:
    #   The root and the number of iterations
    x = x0
    verbose and print('k ={:3d}, x = {:14.10f}'.format(0, x))  
    for k in range(max_iter):        
        x_old = x                        # Store old values for error estimation 
        x = g(x)                         # The iteration
        err = abs(x-x_old)               # Error estimate
        verbose and print('k ={:3d}, x = {:14.10f}'.format(k+1, x))
        if err < tol:                    # The solution is accepted 
            verbose and print("The last step was below the tolerance( {:1.4e}<{:1.4e})".format(err,tol))
            break
    return x, k+1

And the example from slide #9 performs like

In [ ]:
def g(x):       
    return (x**3+x**2-3)/3

# Since we know the solutions from before - are these fixed points?
[g(-math.sqrt(3)), g(-1), g(math.sqrt(3))]

In [ ]:
# Apply the fixed point scheme
x, nit = fixpoint(g, x0=1.5, tol=10.e-6, max_iter=30)

print('\nx = {} after {} iterations'.format(x, nit))

## Newtons method

The algorithm from slide #17 reads

In [ ]:
def newton(f, df, x0, tol=1.e-8, max_iter=30, verbose=True):
    """
        newton(f, df, x0, tol=1.e-8, max_iter=30, verbose=True):
    
    Solve $f(x) = 0$ by Newtons method.
    
    Input:
        f    - the function f
        df   - the derivative of f
        x0   - initial value
    Optional (keyword) parameters
        tol      - (`1.0e-8`) a tolerance when to stop
        max_iter - (`30`) the maximal number of iterations
        verbose  – (`True`) prints the iterates if set to true
    Output:
        x, k – the found root and the number of iterations needed
               to get to this point
    """
    x = x0
    verbose and print('k ={:3d}, x = {:18.15f}, f(x) = {:10.3e}'.format(0, x, f(x)))
    for k in range(max_iter):
        fx = f(x)
        if abs(fx) < tol:           # Accept the solution 
            verbose and print('The function value {:1.5e} is below the tolerance ({:1.5e})'.format(fx,tol))
            break 
        x = x - fx/df(x)            # Newton-iteration
        verbose and print('k ={:3d}, x = {:18.15f}, f(x) = {:10.3e}'.format(k+1, x, f(x)))
    return x, k+1

And we continue with our example above, we just additionally need its derivative

In [ ]:
def df(x):                  # The derivative f'
    return 3*x**2+2*x-3

# A start value
x0 = 1
# Note that we want to come _really_ close here
x, nit = newton(f, df, x0, tol=1.e-14, max_iter=30)
print('\nResult:\nx={}, number of iterations={}'.format(x, nit))

## Newton's method for systems of equations

From Slide #24 we obtain the algorithm

In [ ]:
def newton_system(f, J, x0, tol = 1.0e-10, max_iter=20, verbose=True):
    """
        newton_system(f, J, x0, tol = 1.e-10, max_iter=20, verbose=True)
    
    Solve the system of equations given by $\mathbf{F}(\mathbf{x}) = 0$ using Newton's method.
    
    Input:
        f    - the function f
        J    - the Jacobian of f
        x0   - initial value
    Optional (keyword) parameters
        tol      - (`1.0e-10`) a tolerance when to stop (maximal movement in a compontent of $\mathbf f(\mathbf x^{(k)})$ is less than this tolerance)
        max_iter - (`20`) the maximal number of iterations
        verbose  – (`True`) prints the iterates if set to true
    Output:
        x, k – the found root and the number of iterations needed
               to get to this point
    """
    x = x0
    verbose and print('k ={:3d}, x = '.format(0), x)
    for k in range(max_iter):
        fx = f(x)
        me = norm(fx, math.inf)
        if me < tol: # Maximal entry if suze less than tol
            verbose and print('The (max entrywise) function value {:1.5e} is below the tolerance ({:1.5e})'.format(me, tol))
            break
        Jx = J(x)
        delta = solve(Jx, -fx) # Solve (J(x))δ = f(x) 
        x = x + delta            
        verbose and print('k ={:3d}, x = '.format(k+1), x)
    return x, k

The example form slide #25 reads as follows. Be careful with the indexing: Python starts at 0 so $x_1$ is `x[0]`.

In [ ]:
def f(x):               
    y = np.array([x[0]**3-x[1]+0.25, 
               x[0]**2+x[1]**2-1])
    return y

def J(x):
    return np.array(
         [[3*x[0]**2, -1],
         [2*x[0],    2*x[1]]])

x0 = np.array([1.0, 1.0])          # Starting values
max_iter = 20
# Apply Newton's method
x, nit = newton_system(f, J, x0, tol = 1.e-12, max_iter = max_iter)
  
print('\nTest: f(x)={}'.format(f(x)))
if nit == max_iter:
    printf('Warning: Convergence was not achieved')

In [ ]:
# Slide 26 Example 2
def f(x):               
    y = np.array([x[0]*math.exp(x[1]) - 1,
               -x[0]**2+x[1] - 1)
    return y

                
def J(x):
    return #define the Jacobian yourself
                  
x0 = # Set the starting value
# Apply Newton's method
x, nit = newton_system(f, jac, x0, tol = 1.e-12)

print('\nTest: f(x)={}'.format(f(x)))